In [1]:
import pandas as pd
import numpy as np
import os
import json,pickle
from collections import OrderedDict
from rdkit import Chem
from rdkit.Chem import MolFromSmiles
import networkx as nx
from utils import *


In [2]:
all_3_folds={}
for i in [0,1,2]:
    file_name = 'fold' +str(i)  

    temp = open('./data/kiba/KIBA_3_FOLDS/' + file_name +'.pkl', 'rb')
    new_df = pd.read_pickle(temp)
    all_3_folds.update({file_name:new_df})
    temp.close()


In [3]:
# all_3_folds['fold2']

In [4]:
def create_test_train_kiba(fold_number, all_3_folds):
    test_set = pd.DataFrame(columns=['compound_iso_smiles', 'target_sequence', 'affinity'])
    train_set = pd.DataFrame(columns=test_set.columns)
    
    for i in [0,1,2]:
        fold_name = 'fold' + str(i)
        df = all_3_folds[fold_name]
        print(i)
        if str(i) == fold_number:
            for index, row in df.iterrows():
                smi = row['SMILES']
                new_smi = Chem.MolToSmiles(Chem.MolFromSmiles(smi),isomericSmiles=True)
                seq= row['Target Sequence']
                label = row['Label']
                test_set = test_set.append({'compound_iso_smiles':new_smi, 'target_sequence':seq,'affinity': label}, ignore_index=True)
    
        else:
            new_df = pd.DataFrame(columns=test_set.columns)
            for index, row in df.iterrows():
                smi = row['SMILES']
                new_smi = Chem.MolToSmiles(Chem.MolFromSmiles(smi),isomericSmiles=True)
                seq= row['Target Sequence']
                label = row['Label']
                new_df = new_df.append({'compound_iso_smiles':new_smi, 'target_sequence':seq,'affinity': label}, ignore_index=True)
            train_set = pd.concat([train_set,new_df], ignore_index=True)
    return train_set, test_set

In [5]:
train, test = create_test_train_kiba('2', all_3_folds)

0
1
2


In [6]:
test

compound_iso_smiles  \
0                COc1cc2c(cc1Cl)C(c1ccc(Cl)c(Cl)c1)=NCC2   
1                    COc1cc2c(cc1Cl)C(c1cccc(Cl)c1)=NCC2   
2      O=C(Cc1ccccc1)Nc1cccc(-c2nc3sccn3c2-c2ccnc(Nc3...   
3      CN(C)CCN1CCN(C(=O)c2cc(C(C)(C)C)sc2NC(=O)Nc2cc...   
4                             CCOc1nc(NC(C)=O)cc(N)c1C#N   
...                                                  ...   
34047                 Cc1cc(O)cc2oc3cc(O)cc(O)c3c(=O)c12   
34048  C=C(CCC(C)C1CCC2C(CCc3cc(O)ccc3C)C(O)CCC12C)C(C)C   
34049    Cc1ccc(O)cc1CCC1C(O)CCC2(C)C(C(C)CCCC(C)C)CCC12   
34050  Cc1ccc(O)cc1CCC1C(=O)CCC2(C)C(C(C)C=CCC(C)C)CCC12   
34051  CN1CCN(c2ccc(Nc3ncc4nc(Nc5ccccc5)n(C5CCCC5)c4n...   

                                         target_sequence   affinity  
0      MGPGVLLLLLVATAWHGQGIPVIEPSVPELVVKPGATVTLRCVGNG...  11.100000  
1      MGPGVLLLLLVATAWHGQGIPVIEPSVPELVVKPGATVTLRCVGNG...  11.100000  
2      MGPGVLLLLLVATAWHGQGIPVIEPSVPELVVKPGATVTLRCVGNG...  12.213943  
3      MGPGVLLLLLVATAWHGQGIPVIEPSVPELVVKPGATVTLRCVGNG...  10.622879  
4      MGPGVLLLLLVATAWHGQGIPVIEPSVPELVVKPGATVTLRCVGNG...  11.701030  
...                                                  ...        ...  
34047  MASDAVQSEPRSWSLLEQLGLAGADLAAPGVQQQLELERERLRREI...  10.360428  
34048  MASDAVQSEPRSWSLLEQLGLAGADLAAPGVQQQLELERERLRREI...  10.100000  
34049  MASDAVQSEPRSWSLLEQLGLAGADLAAPGVQQQLELERERLRREI...  10.100000  
34050  MASDAVQSEPRSWSLLEQLGLAGADLAAPGVQQQLELERERLRREI...  10.100000  
34051  MASDAVQSEPRSWSLLEQLGLAGADLAAPGVQQQLELERERLRREI...  11.314670  

[34052 rows x 3 columns]

In [7]:
# test_smiles = list(test['compound_iso_smiles'])
# test_targets = list(test['target_sequence'])
# train_smiles = list(train['compound_iso_smiles'])
# train_targets = list(train['target_sequence'])

# # for i in test_smiles:
# #     if i in train_smiles:
# #         print("common entity present")
# for i in test_targets:
#     if i in train_targets:
#         print("common entity present")

In [8]:
test.to_csv('./data/kiba_test.csv', index=False)
train.to_csv('./data/kiba_train.csv', index=False)

In [8]:
# test = pd.read_csv('./data/kiba_test_fold0.csv')
# train = pd.read_csv('./data/kiba_train_fold0.csv')


In [9]:
def atom_features(atom):
    return np.array(one_of_k_encoding_unk(atom.GetSymbol(),['C', 'N', 'O', 'S', 'F', 'Si', 'P', 'Cl', 'Br', 'Mg', 'Na','Ca', 'Fe', 'As', 'Al', 'I', 'B', 'V', 'K', 'Tl', 'Yb','Sb', 'Sn', 'Ag', 'Pd', 'Co', 'Se', 'Ti', 'Zn', 'H','Li', 'Ge', 'Cu', 'Au', 'Ni', 'Cd', 'In', 'Mn', 'Zr','Cr', 'Pt', 'Hg', 'Pb', 'Unknown']) +
                    one_of_k_encoding(atom.GetDegree(), [0, 1, 2, 3, 4, 5, 6,7,8,9,10]) +
                    one_of_k_encoding_unk(atom.GetTotalNumHs(), [0, 1, 2, 3, 4, 5, 6,7,8,9,10]) +
                    one_of_k_encoding_unk(atom.GetImplicitValence(), [0, 1, 2, 3, 4, 5, 6,7,8,9,10]) +
                    [atom.GetIsAromatic()])

def one_of_k_encoding(x, allowable_set):
    if x not in allowable_set:
        raise Exception("input {0} not in allowable set{1}:".format(x, allowable_set))
    return list(map(lambda s: x == s, allowable_set))

def one_of_k_encoding_unk(x, allowable_set):
    """Maps inputs not in the allowable set to the last element."""
    if x not in allowable_set:
        x = allowable_set[-1]
    return list(map(lambda s: x == s, allowable_set))

def smile_to_graph(smile):
    mol = Chem.MolFromSmiles(smile)
    
    c_size = mol.GetNumAtoms()
    
    features = []
    for atom in mol.GetAtoms():
        feature = atom_features(atom)
        features.append( feature / sum(feature) )

    edges = []
    for bond in mol.GetBonds():
        edges.append([bond.GetBeginAtomIdx(), bond.GetEndAtomIdx()])
    g = nx.Graph(edges).to_directed()
    edge_index = []
    for e1, e2 in g.edges:
        edge_index.append([e1, e2])
        
    return c_size, features, edge_index

def seq_cat(prot):
    x = np.zeros(max_seq_len)
    for i, ch in enumerate(prot[:max_seq_len]): 
        x[i] = seq_dict[ch]
    return x  



In [10]:
seq_voc = "ABCDEFGHIKLMNOPQRSTUVWXYZ"
seq_dict = {v:(i+1) for i,v in enumerate(seq_voc)}
seq_dict_len = len(seq_dict)
max_seq_len = 1000


In [11]:
compound_iso_smiles = []
for dt_name in ['kiba']:
    opts = ['train','test']
    for opt in opts:
        df = pd.read_csv('data/' + dt_name + '_' + opt + '.csv')
        compound_iso_smiles += list( df['compound_iso_smiles'] )
compound_iso_smiles = set(compound_iso_smiles)
smile_graph = {}
for smile in compound_iso_smiles:
    g = smile_to_graph(smile)
    smile_graph[smile] = g

datasets = ['davis', 'kiba']
dataset = datasets[1]

In [12]:
# train set
df = pd.read_csv('data/' + dataset + '_train.csv')
train_drugs, train_prots,  train_Y = list(df['compound_iso_smiles']),list(df['target_sequence']),list(df['affinity'])
XT = [seq_cat(t) for t in train_prots]
train_drugs, train_prots,  train_Y = np.asarray(train_drugs), np.asarray(XT), np.asarray(train_Y)

# test set
df = pd.read_csv('data/' + dataset + '_test.csv')
test_drugs, test_prots,  test_Y = list(df['compound_iso_smiles']),list(df['target_sequence']),list(df['affinity'])
XT = [seq_cat(t) for t in test_prots]
test_drugs, test_prots,  test_Y = np.asarray(test_drugs), np.asarray(XT), np.asarray(test_Y)


In [13]:
processed_data_file_train = 'data/processed/' + dataset + '_train.pt'
processed_data_file_test = 'data/processed/' + dataset + '_test.pt'

In [14]:

# make data PyTorch Geometric ready
print('preparing ', dataset + '_train.pt in pytorch format!')
train_data = TestbedDataset(root='data', dataset=dataset+'_train', xd=train_drugs, xt=train_prots, y=train_Y,smile_graph=smile_graph)
print('preparing ', dataset + '_test.pt in pytorch format!')
test_data = TestbedDataset(root='data', dataset=dataset+'_test', xd=test_drugs, xt=test_prots, y=test_Y,smile_graph=smile_graph)
print(processed_data_file_train, ' and ', processed_data_file_test, ' have been created')

preparing  kiba_train.pt in pytorch format!
Pre-processed data data/processed/kiba_train.pt not found, doing pre-processing...
Converting SMILES to graph: 1/84202
Converting SMILES to graph: 2/84202
Converting SMILES to graph: 3/84202
Converting SMILES to graph: 4/84202
Converting SMILES to graph: 5/84202
Converting SMILES to graph: 6/84202
Converting SMILES to graph: 7/84202
Converting SMILES to graph: 8/84202
Converting SMILES to graph: 9/84202
Converting SMILES to graph: 10/84202
Converting SMILES to graph: 11/84202
Converting SMILES to graph: 12/84202
Converting SMILES to graph: 13/84202
Converting SMILES to graph: 14/84202
Converting SMILES to graph: 15/84202
Converting SMILES to graph: 16/84202
Converting SMILES to graph: 17/84202
Converting SMILES to graph: 18/84202
Converting SMILES to graph: 19/84202
Converting SMILES to graph: 20/84202
Converting SMILES to graph: 21/84202
Converting SMILES to graph: 22/84202
Converting SMILES to graph: 23/84202
Converting SMILES to graph: 24/

Converting SMILES to graph: 247/84202
Converting SMILES to graph: 248/84202
Converting SMILES to graph: 249/84202
Converting SMILES to graph: 250/84202
Converting SMILES to graph: 251/84202
Converting SMILES to graph: 252/84202
Converting SMILES to graph: 253/84202
Converting SMILES to graph: 254/84202
Converting SMILES to graph: 255/84202
Converting SMILES to graph: 256/84202
Converting SMILES to graph: 257/84202
Converting SMILES to graph: 258/84202
Converting SMILES to graph: 259/84202
Converting SMILES to graph: 260/84202
Converting SMILES to graph: 261/84202
Converting SMILES to graph: 262/84202
Converting SMILES to graph: 263/84202
Converting SMILES to graph: 264/84202
Converting SMILES to graph: 265/84202
Converting SMILES to graph: 266/84202
Converting SMILES to graph: 267/84202
Converting SMILES to graph: 268/84202
Converting SMILES to graph: 269/84202
Converting SMILES to graph: 270/84202
Converting SMILES to graph: 271/84202
Converting SMILES to graph: 272/84202
Converting S

Converting SMILES to graph: 497/84202
Converting SMILES to graph: 498/84202
Converting SMILES to graph: 499/84202
Converting SMILES to graph: 500/84202
Converting SMILES to graph: 501/84202
Converting SMILES to graph: 502/84202
Converting SMILES to graph: 503/84202
Converting SMILES to graph: 504/84202
Converting SMILES to graph: 505/84202
Converting SMILES to graph: 506/84202
Converting SMILES to graph: 507/84202
Converting SMILES to graph: 508/84202
Converting SMILES to graph: 509/84202
Converting SMILES to graph: 510/84202
Converting SMILES to graph: 511/84202
Converting SMILES to graph: 512/84202
Converting SMILES to graph: 513/84202
Converting SMILES to graph: 514/84202
Converting SMILES to graph: 515/84202
Converting SMILES to graph: 516/84202
Converting SMILES to graph: 517/84202
Converting SMILES to graph: 518/84202
Converting SMILES to graph: 519/84202
Converting SMILES to graph: 520/84202
Converting SMILES to graph: 521/84202
Converting SMILES to graph: 522/84202
Converting S

Converting SMILES to graph: 749/84202
Converting SMILES to graph: 750/84202
Converting SMILES to graph: 751/84202
Converting SMILES to graph: 752/84202
Converting SMILES to graph: 753/84202
Converting SMILES to graph: 754/84202
Converting SMILES to graph: 755/84202
Converting SMILES to graph: 756/84202
Converting SMILES to graph: 757/84202
Converting SMILES to graph: 758/84202
Converting SMILES to graph: 759/84202
Converting SMILES to graph: 760/84202
Converting SMILES to graph: 761/84202
Converting SMILES to graph: 762/84202
Converting SMILES to graph: 763/84202
Converting SMILES to graph: 764/84202
Converting SMILES to graph: 765/84202
Converting SMILES to graph: 766/84202
Converting SMILES to graph: 767/84202
Converting SMILES to graph: 768/84202
Converting SMILES to graph: 769/84202
Converting SMILES to graph: 770/84202
Converting SMILES to graph: 771/84202
Converting SMILES to graph: 772/84202
Converting SMILES to graph: 773/84202
Converting SMILES to graph: 774/84202
Converting S

Converting SMILES to graph: 996/84202
Converting SMILES to graph: 997/84202
Converting SMILES to graph: 998/84202
Converting SMILES to graph: 999/84202
Converting SMILES to graph: 1000/84202
Converting SMILES to graph: 1001/84202
Converting SMILES to graph: 1002/84202
Converting SMILES to graph: 1003/84202
Converting SMILES to graph: 1004/84202
Converting SMILES to graph: 1005/84202
Converting SMILES to graph: 1006/84202
Converting SMILES to graph: 1007/84202
Converting SMILES to graph: 1008/84202
Converting SMILES to graph: 1009/84202
Converting SMILES to graph: 1010/84202
Converting SMILES to graph: 1011/84202
Converting SMILES to graph: 1012/84202
Converting SMILES to graph: 1013/84202
Converting SMILES to graph: 1014/84202
Converting SMILES to graph: 1015/84202
Converting SMILES to graph: 1016/84202
Converting SMILES to graph: 1017/84202
Converting SMILES to graph: 1018/84202
Converting SMILES to graph: 1019/84202
Converting SMILES to graph: 1020/84202
Converting SMILES to graph: 1

...

Converting SMILES to graph: 33058/34052
Converting SMILES to graph: 33059/34052
Converting SMILES to graph: 33060/34052
Converting SMILES to graph: 33061/34052
Converting SMILES to graph: 33062/34052
Converting SMILES to graph: 33063/34052
Converting SMILES to graph: 33064/34052
Converting SMILES to graph: 33065/34052
Converting SMILES to graph: 33066/34052
Converting SMILES to graph: 33067/34052
Converting SMILES to graph: 33068/34052
Converting SMILES to graph: 33069/34052
Converting SMILES to graph: 33070/34052
Converting SMILES to graph: 33071/34052
Converting SMILES to graph: 33072/34052
Converting SMILES to graph: 33073/34052
Converting SMILES to graph: 33074/34052
Converting SMILES to graph: 33075/34052
Converting SMILES to graph: 33076/34052
Converting SMILES to graph: 33077/34052
Converting SMILES to graph: 33078/34052
Converting SMILES to graph: 33079/34052
Converting SMILES to graph: 33080/34052
Converting SMILES to graph: 33081/34052
Converting SMILES to graph: 33082/34052


Converting SMILES to graph: 33299/34052
Converting SMILES to graph: 33300/34052
Converting SMILES to graph: 33301/34052
Converting SMILES to graph: 33302/34052
Converting SMILES to graph: 33303/34052
Converting SMILES to graph: 33304/34052
Converting SMILES to graph: 33305/34052
Converting SMILES to graph: 33306/34052
Converting SMILES to graph: 33307/34052
Converting SMILES to graph: 33308/34052
Converting SMILES to graph: 33309/34052
Converting SMILES to graph: 33310/34052
Converting SMILES to graph: 33311/34052
Converting SMILES to graph: 33312/34052
Converting SMILES to graph: 33313/34052
Converting SMILES to graph: 33314/34052
Converting SMILES to graph: 33315/34052
Converting SMILES to graph: 33316/34052
Converting SMILES to graph: 33317/34052
Converting SMILES to graph: 33318/34052
Converting SMILES to graph: 33319/34052
Converting SMILES to graph: 33320/34052
Converting SMILES to graph: 33321/34052
Converting SMILES to graph: 33322/34052
Converting SMILES to graph: 33323/34052


Converting SMILES to graph: 33547/34052
Converting SMILES to graph: 33548/34052
Converting SMILES to graph: 33549/34052
Converting SMILES to graph: 33550/34052
Converting SMILES to graph: 33551/34052
Converting SMILES to graph: 33552/34052
Converting SMILES to graph: 33553/34052
Converting SMILES to graph: 33554/34052
Converting SMILES to graph: 33555/34052
Converting SMILES to graph: 33556/34052
Converting SMILES to graph: 33557/34052
Converting SMILES to graph: 33558/34052
Converting SMILES to graph: 33559/34052
Converting SMILES to graph: 33560/34052
Converting SMILES to graph: 33561/34052
Converting SMILES to graph: 33562/34052
Converting SMILES to graph: 33563/34052
Converting SMILES to graph: 33564/34052
Converting SMILES to graph: 33565/34052
Converting SMILES to graph: 33566/34052
Converting SMILES to graph: 33567/34052
Converting SMILES to graph: 33568/34052
Converting SMILES to graph: 33569/34052
Converting SMILES to graph: 33570/34052
Converting SMILES to graph: 33571/34052


Converting SMILES to graph: 33782/34052
Converting SMILES to graph: 33783/34052
Converting SMILES to graph: 33784/34052
Converting SMILES to graph: 33785/34052
Converting SMILES to graph: 33786/34052
Converting SMILES to graph: 33787/34052
Converting SMILES to graph: 33788/34052
Converting SMILES to graph: 33789/34052
Converting SMILES to graph: 33790/34052
Converting SMILES to graph: 33791/34052
Converting SMILES to graph: 33792/34052
Converting SMILES to graph: 33793/34052
Converting SMILES to graph: 33794/34052
Converting SMILES to graph: 33795/34052
Converting SMILES to graph: 33796/34052
Converting SMILES to graph: 33797/34052
Converting SMILES to graph: 33798/34052
Converting SMILES to graph: 33799/34052
Converting SMILES to graph: 33800/34052
Converting SMILES to graph: 33801/34052
Converting SMILES to graph: 33802/34052
Converting SMILES to graph: 33803/34052
Converting SMILES to graph: 33804/34052
Converting SMILES to graph: 33805/34052
Converting SMILES to graph: 33806/34052


Converting SMILES to graph: 34015/34052
Converting SMILES to graph: 34016/34052
Converting SMILES to graph: 34017/34052
Converting SMILES to graph: 34018/34052
Converting SMILES to graph: 34019/34052
Converting SMILES to graph: 34020/34052
Converting SMILES to graph: 34021/34052
Converting SMILES to graph: 34022/34052
Converting SMILES to graph: 34023/34052
Converting SMILES to graph: 34024/34052
Converting SMILES to graph: 34025/34052
Converting SMILES to graph: 34026/34052
Converting SMILES to graph: 34027/34052
Converting SMILES to graph: 34028/34052
Converting SMILES to graph: 34029/34052
Converting SMILES to graph: 34030/34052
Converting SMILES to graph: 34031/34052
Converting SMILES to graph: 34032/34052
Converting SMILES to graph: 34033/34052
Converting SMILES to graph: 34034/34052
Converting SMILES to graph: 34035/34052
Converting SMILES to graph: 34036/34052
Converting SMILES to graph: 34037/34052
Converting SMILES to graph: 34038/34052
Converting SMILES to graph: 34039/34052
